# Análasis de dependencia de Quimicos - TratamientoJugo

Se desea validar la dependencia de los quimicos para la producción de unos procesos, y el impacto en las etapas del proceso.

El objetivo sera demostrar con analisis estadistico el nivel de dependencia de las variables, los valores que hacen que incremente o disminuya.

### Cargamos los datos

In [1]:
import pandas as pd
import numpy as np
import sklearn.model_selection as skmodel
import warnings
from sklearn.linear_model import ElasticNet
from sklearn.linear_model import LinearRegression
import sklearn.metrics as skmetrics
from sklearn.model_selection import KFold, cross_validate
import sklearn.model_selection as skmodel
import plotly.graph_objects as go
from plotly.subplots import make_subplots
warnings.filterwarnings("ignore")
from statsmodels.formula.api import ols
import statsmodels.api as sm

import scipy.stats
import matplotlib.pyplot as plt
%matplotlib inline

import math
import cufflinks as cf
cf.set_config_file(sharing='public', theme='ggplot', offline=True)
cf.getThemes()

['ggplot', 'pearl', 'solar', 'space', 'white', 'polar', 'henanigans']

In [2]:
dataset = pd.read_excel("./DataSet_ValidaQuimicos.xlsx", header=3, sheet_name='Q_TratamientoJugo')
dataset=dataset.dropna()
dataset.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 191 entries, 0 to 190
Data columns (total 56 columns):
 #   Column                                       Non-Null Count  Dtype         
---  ------                                       --------------  -----         
 0   Semana                                       191 non-null    int64         
 1   Fecha                                        191 non-null    datetime64[ns]
 2   dia                                          191 non-null    int64         
 3   Cal (kg/t Caña)                              191 non-null    int64         
 4   Azufre (kg/t Azúcar Blanco)                  191 non-null    int64         
 5   Ácido Fosfórico (kg/t Caña)                  191 non-null    float64       
 6   Ácido Sulfámico (kg/t Caña)                  191 non-null    int64         
 7   Soda Cáustica (l/t Caña)                     191 non-null    float64       
 8   Floculante de Jugo (kg/t Caña)               191 non-null    int64         
 9  

#### Agregacion por semana

In [3]:
df_semana = dataset.astype({"Semana": int})
df_semana = df_semana.groupby(by=["Semana"], dropna=False).mean()
df_semana.reset_index(inplace= True)
df_semana

Semana    dia  Cal (kg/t Caña)  Azufre (kg/t Azúcar Blanco)  \
0        1    2.0     51237.000000                  3070.000000   
1        2    8.0     43847.857143                  4085.714286   
2        3   15.0     33689.285714                  4364.285714   
3        4   22.0     31072.857143                  2871.428571   
4        5   29.0     31226.428571                  4964.285714   
5        6   36.0     33837.142857                  5592.857143   
6        7   43.0     41755.000000                  4078.571429   
7        8   50.0     30670.000000                  3871.428571   
8        9   57.0     43862.857143                  5578.571429   
9       10   64.0     31182.142857                  5728.571429   
10      11   71.0     40499.285714                  5814.285714   
11      12   78.0      1264.285714                  5807.142857   
12      13   85.0     80332.857143                  6285.714286   
13      14   92.0     50227.857143                  6071.428571   
14      15   99.0     49288.571429                  4750.000000   
15      16  106.0       853.571429                  4285.714286   
16      17  113.0    102168.571429                  4642.857143   
17      18  120.0     43955.714286                  5592.857143   
18      19  127.0     47385.714286                  5435.714286   
19      20  134.0     47012.142857                  5085.714286   
20      21  141.0     23148.571429                  4921.428571   
21      22  148.0     62770.000000                  4585.714286   
22      23  155.0     42282.857143                  5392.857143   
23      24  162.0     47377.857143                  6350.000000   
24      25  169.0     37179.285714                  6685.714286   
25      26  176.0     44933.571429                  6707.142857   
26      27  183.0     30426.428571                  6250.000000   
27      28  188.5       243.750000                     0.000000   

    Ácido Fosfórico (kg/t Caña)  Ácido Sulfámico (kg/t Caña)  \
0                   3060.000000                          0.0   
1                   3474.285714                          0.0   
2                   4205.714286                          0.0   
3                   2701.714286                          0.0   
4                   3034.771429                          0.0   
5                   3600.385714                          0.0   
6                   3242.971429                          0.0   
7                   2702.400000                          0.0   
8                   3757.742857                          0.0   
9                   3824.171429                          0.0   
10                  2094.714286                          0.0   
11                  2285.142857                          0.0   
12                  1904.285714                          0.0   
13                  2024.000000                          0.0   
14                  2074.971429                          0.0   
15                  1718.571429                          0.0   
16                  1622.914286                          0.0   
17                  1572.828571                          0.0   
18                  2323.028571                          0.0   
19                  1888.891429                          0.0   
20                  1928.571429                          0.0   
21                  1897.142857                          0.0   
22                  2142.857143                          0.0   
23                  2111.428571                          0.0   
24                  1740.000000                          0.0   
25                  2194.285714                          0.0   
26                  1462.857143                          0.0   
27                   330.000000                          0.0   

    Soda Cáustica (l/t Caña)  Floculante de Jugo (kg/t Caña)  \
0                5830.597505                      180.000000   
1                2081.418253                      196.285714   
2          

## Definimos las Variables (Y's) a Analizar

In [4]:
def get_ys(df):
    ys=[]
    for i in df.iloc[:,27:].columns:
        if not (i.__contains__('X')):
            ys.append(i)
    return ys

In [5]:
ys=get_ys(df_semana)
ys

['Y_pHJugoAlcalizado_17_+',
 'Y_ColorJugoClaro_19_-',
 'Y_ColorAzucarBlanco_18_-',
 'YA_TurbidezJugoClaro_19_-',
 'YA_TransmitanciaJugoClaro_18_+',
 'Y_BrixMeladuraEvaporada_22_+',
 'Y_TiempoPerdidoEvaporacion_22_-',
 'YFJ_TurbidezJugoClaro_23_-',
 'YFJ_TransmitanciaJugoClaro_23_+',
 'Y_PolCachaza_24_-',
 'YFC_TransmitanciaJugoClaro_24_+',
 'YFC_TurbidezJugoClaro_24_-',
 'Y_TurbidezMeladuraClarificada_25_-',
 'Y_TransmitanciaMeladuraClarificada_25_+',
 'Y_ColorMeladuraClarificada_25_-',
 'Y_TurbidezMeladuraClarificada_40_-',
 'Y_TransmitanciaMeladuraClarificada_40_+',
 'Y_ColorMeladuraClarificada_40_-',
 'YD_TurbidezMeladuraClarificada_26_-',
 'YD_TransmitanciaMeladuraClarificada_26_+',
 'YD_ColorMeladuraClarificada_26_-',
 'YD_TurbidezMeladuraClarificada_47_-',
 'YD_TransmitanciaMeladuraClarificada_47_+',
 'YD_ColorMeladuraClarificada_47_-',
 'Y_CaidaPurezaJugoPrimarioDiluido_27_-',
 'Y_pHJugoDiluido_27_-']

## Lista pares Variable vs Químico

Se realizo una función para poder visualizar los pares Variable vs Químico previo a su análisis.

In [6]:
def list_quimicos(df):
    ys = get_ys(df)
    lista_quimicos = []
    lista_quimicos_completa = []
    for y in ys:
        sep = y.split(sep='_')
        name_y = '_'.join(sep[1:2])
        posx= int(sep[-2])-1
        complete_x_name = df.iloc[:,posx:posx+1].columns[0]
        name_x = ''.join((df.iloc[:,posx:posx+1].columns[0]).split(sep='_')[1:])
        lista_quimicos.append(name_y + ' ~ ' + name_x)
        lista_quimicos_completa.append(y + ' ~ ' + complete_x_name)

    return lista_quimicos, lista_quimicos_completa

In [7]:
list_quimicos(df_semana)

(['pHJugoAlcalizado ~ CAL',
  'ColorJugoClaro ~ AZUFRECAÑA',
  'ColorAzucarBlanco ~ AZUFREAZBLANCO',
  'TurbidezJugoClaro ~ AZUFRECAÑA',
  'TransmitanciaJugoClaro ~ AZUFREAZBLANCO',
  'BrixMeladuraEvaporada ~ SODACAUSTICA',
  'TiempoPerdidoEvaporacion ~ SODACAUSTICA',
  'TurbidezJugoClaro ~ FLOCULANTEJUGO',
  'TransmitanciaJugoClaro ~ FLOCULANTEJUGO',
  'PolCachaza ~ FLOCULANTECACHAZA',
  'TransmitanciaJugoClaro ~ FLOCULANTECACHAZA',
  'TurbidezJugoClaro ~ FLOCULANTECACHAZA',
  'TurbidezMeladuraClarificada ~ FLOCULANTEMELADURA',
  'TransmitanciaMeladuraClarificada ~ FLOCULANTEMELADURA',
  'ColorMeladuraClarificada ~ FLOCULANTEMELADURA',
  'TurbidezMeladuraClarificada ~ FCBrixMeladuraEvaporada',
  'TransmitanciaMeladuraClarificada ~ FCBrixMeladuraEvaporada',
  'ColorMeladuraClarificada ~ FCBrixMeladuraEvaporada',
  'TurbidezMeladuraClarificada ~ DECOLORANTES',
  'TransmitanciaMeladuraClarificada ~ DECOLORANTES',
  'ColorMeladuraClarificada ~ DECOLORANTES',
  'TurbidezMeladuraClarificada

## Analisis general grafico de la dependencia de variables

In [8]:
datos = {
    'Indice' : ['I_CAL','I_AZUFRE_AZ_BLANCO' ,'I_ACIDO_FOSFORICO','I_SODA_CAUSTICA','I_FLOCULANTE_JUGO','I_FLOCULANTE_CACHAZA','I_FLOCULANTE_MELADURA','I_DECOLORANTES','I_BACTERICIDA','I_AZUFRE_CAÑA','I_ACIDO_SULFAMICO'],
    'Nombre' : ['Cal (kg/t Caña)','Azufre (kg/t Azúcar Blanco)','Ácido Fosfórico (kg/t Caña)','Soda Cáustica (l/t Caña)','Floculante de Jugo (kg/t Caña)','Floculante de Cachaza (kg/t Caña)','Floculante de Meladura (kg/t Azúcar Blanco)','Decolorantes (l/t Azúcar Blanco)','Bactericida (kg/tcaña)','',''],
    'Indice_Inicial': [1.5662,3.0499,0.0931,0.1901,0.0067,0.0066,0.0383,0.2043,0.0036,0,0],
    'Indice_Optimo': [1.4,3.5,0.0931,0.16,0.0055,0.0045,0.0254,0.1,0.003,0,0],
    'Indice_Realista': [1.4,3.5,0.0931,0.1801,0.005,0.005,0.0254,0.15,0.003,0,0],
}

df_indices = pd.DataFrame(datos)
df_indices

Indice                                       Nombre  \
0                   I_CAL                              Cal (kg/t Caña)   
1      I_AZUFRE_AZ_BLANCO                  Azufre (kg/t Azúcar Blanco)   
2       I_ACIDO_FOSFORICO                  Ácido Fosfórico (kg/t Caña)   
3         I_SODA_CAUSTICA                     Soda Cáustica (l/t Caña)   
4       I_FLOCULANTE_JUGO               Floculante de Jugo (kg/t Caña)   
5    I_FLOCULANTE_CACHAZA            Floculante de Cachaza (kg/t Caña)   
6   I_FLOCULANTE_MELADURA  Floculante de Meladura (kg/t Azúcar Blanco)   
7          I_DECOLORANTES             Decolorantes (l/t Azúcar Blanco)   
8           I_BACTERICIDA                       Bactericida (kg/tcaña)   
9           I_AZUFRE_CAÑA                                                
10      I_ACIDO_SULFAMICO                                                

    Indice_Inicial  Indice_Optimo  Indice_Realista  
0           1.5662         1.4000           1.4000  
1           3.0499         3.5000           3.5000  
2           0.0931         0.0931           0.0931  
3           0.1901         0.1600           0.1801  
4           0.0067         0.0055           0.0050  
5           0.0066         0.0045           0.0050  
6           0.0383         0.0254           0.0254  
7           0.2043         0.1000           0.1500  
8           0.0036         0.0030           0.0030  
9           0.0000         0.0000           0.0000  
10          0.0000         0.0000           0.0000

In [10]:
import plotly.figure_factory as ff
def graphs_multi(df,y):
    sep=y.split(sep='_')
    name_y='_'.join(sep[:2])
    posx= int(sep[-2])-1
    name_x=df.iloc[:,posx:posx+1].columns[0]
    data_clean=df.drop(df[df[name_x]==0].index)
    q3=data_clean[name_x].quantile(0.75)
    q1=data_clean[name_x].quantile(0.25)
    iqr=q3-q1
    upper=q3+1.75*iqr
    lower=q1-1.75*iqr
    outliers_indx=data_clean[(data_clean[name_x]>upper) | (data_clean[name_x]<lower) | (data_clean['Caña Recibida']<23000)].index
    data_clean=data_clean.drop(outliers_indx)
    
    x1 = data_clean[name_x]
    y1 = data_clean[y]
    ignore=['X_FC_BrixMeladuraEvaporada', 'X_D_BrixMeladuraEvaporada', 'I_AZUFRE_CAÑA', 'I_ACIDO_SULFAMICO']
    stat, p = scipy.stats.pearsonr(x1, y1)
    print("Coeficiente de Correllacion de Pearson: ",stat)
    print("p-value: ",p)
    
    
    fig = make_subplots(
                rows=3, cols=2,
                vertical_spacing=0.08,
                specs=[[{'type': 'scatter'}, {'type':'scatter'}],
                       [{'type': 'histogram'}, {'type':'histogram'}],
                       [{'type': 'box'}, {'type':'box'}]]
            )
    
    fig.add_trace(go.Scatter(x=x1, y=y1, mode='markers', showlegend=False, marker_color='orange'), row=1,col=1)
    if not (ignore.__contains__(name_x)):
        ii = df_indices.loc[df_indices['Indice']== name_x]['Indice_Inicial'].values[0]
        io = df_indices.loc[df_indices['Indice']== name_x]['Indice_Optimo'].values[0]
        ir = df_indices.loc[df_indices['Indice']== name_x]['Indice_Realista'].values[0]
        fig.add_vline(x=ii,line_width=3, line_dash="dash", line_color="#6699ff", annotation_text='ii= '+str(ii), annotation_position='top')
        fig.add_vline(x=io,line_width=3, line_dash="dash", line_color="green", annotation_text='io= '+str(io), annotation_position='right')
        fig.add_vline(x=ir,line_width=3, line_dash="dash", line_color="red", annotation_text='ir= '+str(ir),  annotation_position='left')
    fig.add_trace(go.Histogram2dContour(x=x1, y=y1, colorscale='Blues', reversescale=False, showscale=False), row=1, col=1)    
    fig.update_xaxes(title_text=name_x, dtick=(max(x1)-min(x1))/10,row=1, col=1)
    fig.update_yaxes(title_text=name_y, row=1, col=1)
    fig.add_trace(go.Scatter(x=data_clean['Semana'], y=x1, mode='markers', marker_symbol='x', name=name_x, marker_color='#6699ff'), row=1,col=2)
    fig.add_trace(go.Scatter(x=data_clean['Semana'], y=y1, mode='markers', name=name_y, marker_color='#8fbc8f'), row=1,col=2)
    fig.update_xaxes(title_text='Semana', dtick=1,row=1, col=2)
    fig.update_yaxes(title_text='Valor', row=1, col=2)
    fig.add_trace(go.Histogram(x=x1, name=name_x, nbinsx=20,showlegend=False, marker_color='#6699ff',marker_line_width=1, marker_line_color='white'), row=2, col=1)
    fig.update_xaxes(title_text=name_x,row=2, col=1)
    fig.add_trace(go.Histogram(x=y1, name=name_y,nbinsx=20, showlegend=False, marker_color='#8fbc8f',marker_line_width=1, marker_line_color='white'), row=2, col=2)
    fig.update_xaxes(title_text=name_y, row=2, col=2)
    fig.add_trace(go.Box(y=x1, showlegend=False, marker_color='#6699ff'), row=3, col=1)
    fig.update_xaxes(title_text=name_x, row=3, col=1)
    fig.add_trace(go.Box(y=y1, showlegend=False, marker_color='#8fbc8f'), row=3, col=2)
    fig.update_xaxes(title_text=name_y, row=3, col=2)
    fig.update_layout(height=1300,hovermode='x', legend=dict(orientation="h",
                                                            yanchor="bottom",
                                                            y=1,
                                                            xanchor="right",
                                                            x=1))
    fig.show()

In [11]:
for i in ys:
    graphs_multi(df_semana, i)

Coeficiente de Correllacion de Pearson:  0.07730602580267855
p-value:  0.7390836049816719


Coeficiente de Correllacion de Pearson:  0.12535101242165053
p-value:  0.5783279049609811


Coeficiente de Correllacion de Pearson:  0.3335312448660366
p-value:  0.10324472051397149


Coeficiente de Correllacion de Pearson:  0.19944080103316553
p-value:  0.3735501698088378


Coeficiente de Correllacion de Pearson:  -0.4710717127634985
p-value:  0.01746022153325557


...

Coeficiente de Correllacion de Pearson:  -0.17594217713135493
p-value:  0.4001997972517872


Coeficiente de Correllacion de Pearson:  -0.08233637081485795
p-value:  0.6955971050671895


Coeficiente de Correllacion de Pearson:  0.16150618587568158
p-value:  0.440545353651307


Coeficiente de Correllacion de Pearson:  -0.15632412931700257
p-value:  0.4555401966954344


Coeficiente de Correllacion de Pearson:  0.7628074387216821
p-value:  9.272777711394543e-06


## Con un scatter plot, graficamos la correlación entre cada Variable a analizar y su respectivo Químico

Se realizaron ciertos filtros y limpieza en los datos.

#### **Outliers:**

1-. **Ceros:** El primer paso es limpiar los datos eliminando todas las filas del par Variable vs Químico, donde la variable contenga un valor igual a 0, ya que representa que no se tomo medida ese día.

2-. **Outliers:** Se identificaron los outliers existentes en cada Variable vs Químico, con un criterio por rango intercuartilico. Se considera un outlier aquel valor que cumpla con una de las sigueintes dos condiciones: 
* El valor es menor que el primer cuartil menos 1.75 veces el rango intercuartilico.
* El valor es mayor que el tercer cuartil más 1.75 veces el rango intercuartilico.

3-. **Caña Recibida:** Se identificaron los casos donde la Caña Recibida no estuvo dentro del rango aceptable o promedio por día. El valor para escoger estos casos fue todo aquel arriba de 23,000. Esto se realizo dado que si no se obtuvo al menos un valor de 23,000 en caña recibida, es muy probable que haya ocurrido imprevistos en producción, como apagones u algun otro inconveniente, convirtiendo esos casos en otro tipo de outliers.

**OBSERVACION:** En cada gráfica se podrá observar el valor de la correlación encontrada.

In [12]:
def graph_corr(df,y):
    sep=y.split(sep='_')
    name_y='_'.join(sep[:2])
    posx= int(sep[-2])-1
    name_x=df.iloc[:,posx:posx+1].columns[0]
    data_clean=df.drop(df[df[name_x]==0].index)
    q3=data_clean[name_x].quantile(0.75)
    q1=data_clean[name_x].quantile(0.25)
    iqr=q3-q1
    upper=q3+1.75*iqr
    lower=q1-1.75*iqr
    outliers_indx=data_clean[(data_clean[name_x]>upper) | (data_clean[name_x]<lower) | (data_clean['Caña Recibida']<23000)].index
    data_clean=data_clean.drop(outliers_indx)
    fig = px.scatter(data_clean, x=name_x, y=i,labels={i:name_y})
    fig.add_trace(go.Indicator(mode="number",
                                value=np.corrcoef(data_clean[name_x],data_clean[i])[0,1],
                                title={'text':'Correlación'},
                                domain = {'y': [0.85, 0.9], 'x': [0.92, 1]}))

    fig.show()

In [13]:
import plotly.express as px
df = px.data.iris()
for i in ys:
    graph_corr(df_semana,i)

## Graficamos la serie de tiempo correspondiente a cada par Variable a analizar.

Se decidio realizar este tipo de gráfica dado que es importante comprender como es el desarrollo y comportamiento de cada variable a lo largo de la Zafra.

**OBSERVACION**: En este caso especifico de las series de tiempo, no se elimino ningun outlier, ya que lo que importa ver en este tipo de gráficas es el desarrollo diario de las Variables y poder determinar si existen patrones respecto al tiempo.

In [14]:
for i in ys:
    sep=i.split(sep='_')
    name_y='_'.join(sep[:2])
    y_plot=df_semana[i]
    y_plot=y_plot.reset_index().rename(columns={'index':'SEMANA'})
    fig = px.line(y_plot,x='SEMANA', y=i)
    fig.update_layout(
                title= 'Time Series of ' + name_y,
                yaxis_title=name_y,
                hovermode='x'
                
    )
    fig.show()

## Graficando la distribución de puntos para cada par Variable vs Químico, agregando lineas de tendencia.

La idea con este tipo de gráficas es poder visualizar y entender como es que reacciona cada Variable respecto al incremento/decremento del Químico.

##### **Lineas de Tendencias:**

Se trabajaron dos lineas de tendencia:

1. Lineal: representada por una ecuación de una recta: y=ax + b.
2. Polinomial: representada por una ecuación de un polinomio de grado entre 2 y 4.

#### **Métricas:**

* Dentro de cada gráfica, se podrá visualizar el R^2 de la linea de tendencia correspondiente a una recta. 
* Esta métrica ayuda evualuar que tan buen ajuste tiene la linea de tendencia respecto a todos los puntos.

#### **Outliers:**

Nuevamente se realizo el proceso de filtrado y limpieza de los datos para realizar las gráficas:

1-. **Ceros:** El primer paso es limpiar los datos eliminando todas las filas del par Variable vs Químico, donde la variable contenga un valor igual a 0, ya que representa que no se tomo medida ese día.

2-. **Outliers:** Se identificaron los outliers existentes en cada Variable vs Químico, con un criterio por rango intercuartilico. Se considera un outlier aquel valor que cumpla con una de las sigueintes dos condiciones: 
* El valor es menor que el primer cuartil menos 1.75 veces el rango intercuartilico.
* El valor es mayor que el tercer cuartil más 1.75 veces el rango intercuartilico.

3-. **Caña Recibida:** Se identificaron los casos donde la Caña Recibida no estuvo dentro del rango aceptable o promedio por día. El valor para escoger estos casos fue todo aquel arriba de 23,000. Esto se realizo dado que si no se obtuvo al menos un valor de 23,000 en caña recibida, es muy probable que haya ocurrido imprevistos en producción, como apagones u algun otro inconveniente, convirtiendo esos casos en otro tipo de outliers.

--------------------------

##### **OBSERVACION**: En el titulo de cada gráfica se podrá visualizar si, con la cantidad de datos obtenidos, la relación entre Variable y Químico tiene un comportamiento 'valido' o 'invalido'. 

In [15]:
def graph_model(df,y):
    sep=y.split(sep='_')
    name_y='_'.join(sep[:2])
    
    posx= int(sep[-2])-1
    name_x=df.iloc[:,posx:posx+1].columns[0]
    data_clean=df.drop(df[df[name_x]==0].index)
    q3=data_clean[name_x].quantile(0.75)
    q1=data_clean[name_x].quantile(0.25)
    iqr=q3-q1
    upper=q3+1.75*iqr
    lower=q1-1.75*iqr
    outliers_indx=data_clean[(data_clean[name_x]>upper) | (data_clean[name_x]<lower) | (data_clean['Caña Recibida']<23000)].index
    data_clean=data_clean.drop(outliers_indx)
    
    x_model=data_clean[name_x]
    y_model=data_clean[y]
    
    r_dif=2
    r_last=0
    r_new=0
    values=0
    cont=2
    aux=0
    while (r_dif>0.001) & (cont<4):
        values=0
        cont=cont+1
        r_last=r_new
        fiti=np.polyfit(x_model, y_model, cont)
        for i in range(cont+1):
            values=values+fiti[i]*(x_model**(cont-i))
        corr_matrix=np.corrcoef(y_model,values)
        corr=corr_matrix[0,1]
        r_new=corr**2
        if aux>=1:
            r_dif=r_new-r_last
        else:
            r_dif=2
        aux=aux+1
    poly_result=pd.concat([pd.Series(x_model, name=name_x), pd.Series(values, name=name_y)], axis=1).sort_values(by=name_x)
    
    lineal_model=LinearRegression()
    lineal_model.fit(np.array(x_model).reshape(-1, 1), y_model)
    lineal_predict=lineal_model.coef_[0]*x_model + lineal_model.intercept_
    lineal_result=pd.concat([pd.Series(x_model, name=name_x), pd.Series(lineal_predict, name=name_y)], axis=1).sort_values(by=name_x)
    corr_matrix=np.corrcoef(y_model,lineal_predict)
    corr=corr_matrix[0,1]
    r2=corr**2
    
    if lineal_model.coef_[0]<0:
        if sep[-1]=='-':
            note=' (COMPORTAMIENTO VALIDO)'
        else:
            note=' (COMPORTAMIENTO INVALIDO)'  
    else:
        if sep[-1]=='+':
            note=' (COMPORTAMIENTO VALIDO)'
        else:
            note=' (COMPORTAMIENTO INVALIDO)'    
            
    fig = go.Figure([go.Scatter(x=data_clean[name_x], y=data_clean[y], name='data', mode='markers'),
                        go.Scatter(x=lineal_result[name_x], y=lineal_result[name_y], 
                    name='Linear Trending', mode='lines+markers'),
                        go.Scatter(x=poly_result[name_x], y=poly_result[name_y], 
                    name='Polynomial Grade '+str(cont)+ ' Trending', mode='lines+markers')])
    fig.add_trace(go.Indicator(mode="number",
                                value=r2,
                                title={'text':'R2 Lineal'},
                                domain = {'y': [0.85, 0.9], 'x': [0.92, 0.98]}))
    fig.update_layout(
            title=str(name_y)+' vs '+str(name_x),# + note,
            xaxis_title=name_x,
            yaxis_title=name_y,
            hovermode='x'
            
    )
    fig.show()
        

In [16]:
for i in ys:
    graph_model(df_semana,i)

## Graficando la distribución de puntos para cada par Variable vs Químico, agregando un Modelo de predicción.

Se realizó esta gráfica para poder visualizar si los datos de la muestra recibida para cada par Variable vs Químico son suficientes para poder crear un modelo de predicción adecuado.

##### **Métricas:**

Dado que se utilizaron dos tipos de modelos, similares más no iguales, el algoritmo debía escoger el mejor de ellos, por lo que se decidio tomar como métrica de selección el **RMSE** (Root Mean Square Error), buscando el menor de estos.

#### **Modelos y Proceso:**

Los modelos utilizados fueron:
1. Elastic Net 
2. Linear Regresssión

Para ambos casos el proceso de creación del modelo constaba de 4 pasos:
1. Split de datos: 70% train - 30% test (random)
2. Creación y entrenamiento con el 70% de los datos
3. Test con el 30% de los datos.
4. Realizar predicción de todos los valores del respectivo Químico (x)

#### **T-Test:**

Después de crear los modelos, también se realizo un T-Test, para poder mostrar en una tabla debajo de cada gráfica el valor t y su respectivo valor p, con el cual se puede determinar que parametros del modelos son estadisticamente significativos. Se utilizo un α=0.05 para la evaluación del valor p.

#### **Outliers:**

Nuevamente se realizo el proceso de filtrado y limpieza de los datos para realizar las gráficas:

1-. **Ceros:** El primer paso es limpiar los datos eliminando todas las filas del par Variable vs Químico, donde la variable contenga un valor igual a 0, ya que representa que no se tomo medida ese día.

2-. **Outliers:** Se identificaron los outliers existentes en cada Variable vs Químico, con un criterio por rango intercuartilico. Se considera un outlier aquel valor que cumpla con una de las sigueintes dos condiciones: 
* El valor es menor que el primer cuartil menos 1.75 veces el rango intercuartilico.
* El valor es mayor que el tercer cuartil más 1.75 veces el rango intercuartilico.

3-. **Caña Recibida:** Se identificaron los casos donde la Caña Recibida no estuvo dentro del rango aceptable o promedio por día. El valor para escoger estos casos fue todo aquel arriba de 23,000. Esto se realizo dado que si no se obtuvo al menos un valor de 23,000 en caña recibida, es muy probable que haya ocurrido imprevistos en producción, como apagones u algun otro inconveniente, convirtiendo esos casos en otro tipo de outliers.

--------------------------

##### **OBSERVACION**: En la etiqueta de cada gráfica se podrá visualizar el RMSE obtenido por el modelo escogido. Así también cada modelo fue gráficado con su respectivo intervalo de confianza al 95%.

In [17]:
def graph_training_model(df,y):
    sep=y.split(sep='_')
    name_y='_'.join(sep[:2])
    rmses=[]
    posx= int(sep[-2])-1
    name_x=df.iloc[:,posx:posx+1].columns[0]
    data_clean=df.drop(df[df[name_x]==0].index)
    q3=data_clean[name_x].quantile(0.75)
    q1=data_clean[name_x].quantile(0.25)
    iqr=q3-q1
    upper=q3+1.75*iqr
    lower=q1-1.75*iqr
    outliers_indx=data_clean[(data_clean[name_x]>upper) | (data_clean[name_x]<lower) | (data_clean['Caña Recibida']<23000)].index
    data_clean=data_clean.drop(outliers_indx)
    
    x_model=data_clean[name_x]
    y_model=data_clean[y]

    
    X_train, X_test, y_train, y_test = skmodel.train_test_split(x_model, y_model, train_size= 0.7)
    lineal_model=LinearRegression()
    lineal_model.fit(np.array(X_train).reshape(-1, 1), y_train)
    
    test_predictions=lineal_model.predict(np.array(X_test).reshape(-1, 1))
    rmses.append(math.sqrt(skmetrics.mean_squared_error(y_true=y_test, y_pred=test_predictions)))
    
    total_predict=lineal_model.predict(np.array(x_model).reshape(-1, 1))
    lineal_result=pd.concat([pd.DataFrame({name_x:x_model}).reset_index(drop=True),pd.DataFrame({name_y:total_predict}).reset_index(drop=True)], axis=1).sort_values(by=name_x)
    
    residuals_lineal=y_train - lineal_model.predict(np.array(X_train).reshape(-1, 1))
    ci_lineal= np.quantile(residuals_lineal, 0.95)
    if ci_lineal>=0:
        lineal_result['upper']=lineal_result[name_y]+ci_lineal
        lineal_result['lower']=lineal_result[name_y]-ci_lineal
    else:
        lineal_result['upper']=lineal_result[name_y]-ci_lineal
        lineal_result['lower']=lineal_result[name_y]+ci_lineal
    # ----------------------
    elastic_model=ElasticNet(alpha=0.5, l1_ratio=0.5)
    elastic_model.fit(np.array(X_train).reshape(-1, 1), y_train)
    
    
    test_predictions2=elastic_model.predict(np.array(X_test).reshape(-1, 1))
    rmses.append(math.sqrt(skmetrics.mean_squared_error(y_true=y_test, y_pred=test_predictions2)))
    
    total_predict_2=elastic_model.predict(np.array(x_model).reshape(-1, 1))
    elastic_result=pd.concat([pd.DataFrame({name_x:x_model}).reset_index(drop=True),pd.DataFrame({name_y:total_predict_2}).reset_index(drop=True)], axis=1).sort_values(by=name_x)
    
    residuals_elastic=y_train - elastic_model.predict(np.array(X_train).reshape(-1, 1))
    ci_elastic= np.quantile(residuals_elastic, 0.95)
    if ci_elastic>=0:
        elastic_result['upper']=elastic_result[name_y]+ci_elastic
        elastic_result['lower']=elastic_result[name_y]-ci_elastic
    else:
        elastic_result['upper']=elastic_result[name_y]-ci_elastic
        elastic_result['lower']=elastic_result[name_y]+ci_elastic
    #------------------------
    for_ttest=sm.add_constant(X_train)
    model_ttest = sm.OLS(y_train, for_ttest).fit()
    result_ttest=pd.DataFrame({'Parameters':model_ttest.tvalues.index, 't':model_ttest.tvalues.values, 'p_value':model_ttest.pvalues.values})
    result_ttest['Conclusion']=np.where(result_ttest['p_value']<0.05,
                                        'p_value<=α, se rechaza la Hipotesis nula, el parametro es estadisticamente significativo para el modelo',
                                        'p_value>α, no se rechaza la Hipotesis nula, el parametro no es estadisticamente significativo para el modelo')    
    
    
    fig = go.Figure(go.Scatter(x=data_clean[name_x], y=data_clean[y], name='data', mode='markers'))
    if rmses.index(min(rmses))==0:
            fig.add_trace(go.Scatter(x=lineal_result[name_x], y=lineal_result[name_y], name='Lineal Model, RMSE: '+str(min(rmses)), mode='lines+markers'))
            fig.add_trace(go.Scatter(name='Lower Bound',
                                x=lineal_result[name_x],
                                y=lineal_result['lower'],
                                marker=dict(color="#444"),
                                line=dict(width=0),
                                mode='lines',
                                fillcolor='rgba(68, 68, 68, 0.3)',
                                fill='tonexty',
                                showlegend=False))
            fig.add_trace(go.Scatter(name='Upper Bound',
                                x=lineal_result[name_x],
                                y=lineal_result['upper'],
                                marker=dict(color="#444"),
                                line=dict(width=0),
                                mode='lines',
                                fillcolor='rgba(68, 68, 68, 0.3)',
                                fill='tonexty',
                                showlegend=False))
    elif rmses.index(min(rmses))==1:
            fig.add_trace(go.Scatter(x=elastic_result[name_x], y=elastic_result[name_y], name='Elastic Net Model, RMSE: '+str(min(rmses)), mode='lines+markers'))
            fig.add_trace(go.Scatter(name='Lower Bound',
                                x=elastic_result[name_x],
                                y=elastic_result['lower'],
                                marker=dict(color="#444"),
                                line=dict(width=0),
                                mode='lines',
                                fillcolor='rgba(68, 68, 68, 0.3)',
                                fill='tonexty',
                                showlegend=False))
            fig.add_trace(go.Scatter(name='Upper Bound',
                                x=elastic_result[name_x],
                                y=elastic_result['upper'],
                                marker=dict(color="#444"),
                                line=dict(width=0),
                                mode='lines',
                                fillcolor='rgba(68, 68, 68, 0.3)',
                                fill='tonexty',
                                showlegend=False))
    fig.update_layout(
            legend=dict(
                orientation="h",
                yanchor="bottom",
                y=1.02,
                xanchor="right",
                x=1
            ),
            title=str(name_y)+' vs '+str(name_x),
            xaxis_title=name_x,
            yaxis_title=name_y,
            hovermode='x'
    )
    table_t = go.Figure(data=[go.Table(
        header=dict(values=list(['Parameters', 'T', 'p_value', 'Conclusion']),
                    align='center'),
        cells=dict(values=[result_ttest['Parameters'],result_ttest['t'], result_ttest['p_value'], result_ttest['Conclusion']],
                align='center')),
        
    ])
    table_t.update_layout(
            title='T-Test for Model of '+str(name_y)+' vs '+str(name_x)
    )
    sub_fig3 = make_subplots(
                rows=2, cols=1,
                shared_xaxes=True,
                vertical_spacing=0.25,
                specs=[[{"type": "scatter"}],
                    [{"type": "table"}]]
            )

    sub_fig3 = sub_fig3.add_trace(fig.data[0], row=1, col=1)
    sub_fig3 = sub_fig3.add_trace(fig.data[1], row=1, col=1)
    sub_fig3 = sub_fig3.add_trace(fig.data[2], row=1, col=1)
    sub_fig3 = sub_fig3.add_trace(fig.data[3], row=1, col=1)
    sub_fig3 = sub_fig3.add_trace(table_t.data[0], row=2, col=1)
    sub_fig3.update_layout(
            legend=dict(
                orientation="h",
                yanchor="bottom",
                y=1.02,
                xanchor="right",
                x=1
            ),
            height=620,
            title=str(name_y)+' vs '+str(name_x),
            xaxis_title=name_x,
            yaxis_title=name_y,
            hovermode='x')
    sub_fig3.show()
        

In [19]:
for i in ys:
    graph_training_model(df_semana,i)